# The Battle of the Neighborhoods part 2
### Applied Data Science Capstone by Andrew Holman

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction: Business Problem <a name="introduction"></a>
This project is aimed to recommend a new location based on zip code for a restaurant type that is already present in Orange County. This will be done by gathering a list of all current restaurants in the area. From this list, a venue category can be picked to analyze. Ratings of restaurants in that venue category will be retrieved and used to create a ranking system to find the best city to build a new restaurant of the same type. Then, all the zip codes within the city will be listed as possible new locations for the restaurant.

In [1]:
#imports

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

from bs4 import BeautifulSoup #BeautifulSoup

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

from os import environ

print('Libraries imported.')

Libraries imported.


## Data <a name="data"></a>
First, we must gather location data about Orange County. It will be taken from the opendatasoft website. A link is provided in part 1. We can then gather location of restaurants and important information, such as rating, using the Foursquare API. The location of Orange County will be generated algorithmically and approximate addresses of the center will be obtained using **Google Maps API reverse geocoding**. We will also be using folium and geospatial data in order to create choropleth maps to show the frequency of restaurants within a city's limits.

In [2]:
#data set of all US zip codes
df = pd.read_csv('us-zip-code-latitude-and-longitude.csv', sep=';')

#obtain only CA zip codes
df = df[df['State'] == 'CA']

#Restrict to only Orange County cities
df = df[(df['City'] == 'Aliso Viejo') | 
        (df['City'] == 'Anaheim') | 
        (df['City'] == 'Brea') | 
        (df['City'] == 'Buena Park') | 
        (df['City'] == 'Costa Mesa') | 
        (df['City'] == 'Cypress') | 
        (df['City'] == 'Dana Point') | 
        (df['City'] == 'Fountain Valley') | 
        (df['City'] == 'Fullerton') | 
        (df['City'] == 'Garden Grove') | 
        (df['City'] == 'Huntington Beach') | 
        (df['City'] == 'Irvine') | 
        (df['City'] == 'La Habra') | 
        (df['City'] == 'La Palma') | 
        (df['City'] == 'Laguna Beach') | 
        (df['City'] == 'Laguna Hills') | 
        (df['City'] == 'Laguna Niguel') | 
        (df['City'] == 'Laguna Woods') | 
        (df['City'] == 'Lake Forest') | 
        (df['City'] == 'Los Alamitos') | 
        (df['City'] == 'Mission Viejo') | 
        (df['City'] == 'Newport Beach') | 
        (df['City'] == 'Orange') | 
        (df['City'] == 'Placentia') | 
        (df['City'] == 'Rancho Santa Margarita') | 
        (df['City'] == 'San Clemente') | 
        (df['City'] == 'San Juan Capistrano') | 
        (df['City'] == 'Santa Ana') | 
        (df['City'] == 'Seal Beach') | 
        (df['City'] == 'Stanton') | 
        (df['City'] == 'Tustin') | 
        (df['City'] == 'Villa Park') | 
        (df['City'] == 'Westminster') | 
        (df['City'] == 'Yorba Linda') ]

df.reset_index(inplace=True, drop=True)
df = df[['Zip', 'City', 'Latitude', 'Longitude']]
df.head(12)

Zip                 City   Latitude   Longitude
0   92709               Irvine  33.640302 -117.769442
1   92693  San Juan Capistrano  33.555323 -117.564000
2   92837            Fullerton  33.640302 -117.769442
3   92840         Garden Grove  33.785166 -117.934060
4   92856               Orange  33.640302 -117.769442
5   92616               Irvine  33.640302 -117.769442
6   92801              Anaheim  33.844814 -117.953810
7   92841         Garden Grove  33.786915 -117.982240
8   92604               Irvine  33.687620 -117.788520
9   92815              Anaheim  33.640302 -117.769442
10  92823                 Brea  33.918965 -117.832520
11  92680         Garden Grove  33.792124 -117.993561

In [3]:
address = 'Orange County, CA'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinates of Orange County are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of Orange County are 33.7500378, -117.8704931.


We create a map of Orange County with the locations of all the zip code addresses.

In [4]:
# create map of Orange County using latitude and longitude values
map_OC = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, city, zipCode in zip(df['Latitude'], df['Longitude'], df['City'], df['Zip']):
    label = '{}, {}'.format(city, zipCode)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_OC)  
    
map_OC

The credentials and version are stored here for using the Foursquare API.

In [25]:
CLIENT_ID = environ.get('FOURSQUARE_CLIENT_ID') # your Foursquare ID
CLIENT_SECRET = environ.get('FOURSQUARE_CLIENT_SECRET') # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

#print('Your credentials:')
#print('CLIENT_ID: ' + CLIENT_ID)
#print('CLIENT_SECRET:' + CLIENT_SECRET)

We create a function in order to make a dataframe of all the nearby venues to each zip code location within a 2km radius. Then, the function is used to create the dataframe for all the zip codes in Orange County. From this, we can group the data both by zip code and city to see where more restaurants lie.

In [7]:
catId = '4d4b7105d754a06374d81259' # food category
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 2000 # define radius

def getNearbyVenues(names, zipcodes, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, zipcode, lat, lng in zip(names, zipcodes, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&categoryId={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION,
            catId,
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            zipcode,
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['id'],
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City',
                  'Zip',
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue',
                  'Venue ID',
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [8]:
OC_venues = getNearbyVenues(names=df['City'],
                            zipcodes=df['Zip'],
                            latitudes=df['Latitude'],
                            longitudes=df['Longitude']
                            )


Irvine
San Juan Capistrano
Fullerton
Garden Grove
Orange
Irvine
Anaheim
Garden Grove
Irvine
Anaheim
Brea
Garden Grove
Placentia
Fullerton
Yorba Linda
Cypress
Westminster
Huntington Beach
Santa Ana
Villa Park
Irvine
Costa Mesa
San Juan Capistrano
Orange
Fountain Valley
Irvine
Fullerton
Newport Beach
Huntington Beach
Lake Forest
Anaheim
Santa Ana
Santa Ana
Anaheim
Orange
Santa Ana
Buena Park
Santa Ana
Rancho Santa Margarita
Costa Mesa
Huntington Beach
Los Alamitos
Garden Grove
Anaheim
San Clemente
Huntington Beach
Westminster
Huntington Beach
Newport Beach
Fullerton
Anaheim
Santa Ana
Irvine
Anaheim
La Habra
Stanton
Newport Beach
Garden Grove
Brea
San Clemente
Santa Ana
Irvine
Tustin
Anaheim
Aliso Viejo
Anaheim
Anaheim
Costa Mesa
Orange
Laguna Niguel
San Clemente
Fountain Valley
Fullerton
Laguna Beach
Orange
Dana Point
Garden Grove
Laguna Hills
Orange
Westminster
Irvine
Buena Park
Tustin
Irvine
Laguna Niguel
Irvine
Placentia
Garden Grove
Fullerton
Orange
Seal Beach
Mission Viejo
Anaheim
M

In [9]:
print(OC_venues.shape)
OC_venues.head()

(891, 9)


City    Zip  Neighborhood Latitude  Neighborhood Longitude  \
0     Irvine  92709              33.640302             -117.769442   
1     Irvine  92709              33.640302             -117.769442   
2     Irvine  92709              33.640302             -117.769442   
3  Fullerton  92837              33.640302             -117.769442   
4  Fullerton  92837              33.640302             -117.769442   

                  Venue                  Venue ID  Venue Latitude  \
0               Solaria  5337b91d498e75abcd5eff08       33.641483   
1  Zafferano coffee bar  52c6a940498ea6e7b1710fdc       33.641483   
2     Marie Callendar's  4f324dcf19836c91c7ca7dff       33.643339   
3               Solaria  5337b91d498e75abcd5eff08       33.641483   
4  Zafferano coffee bar  52c6a940498ea6e7b1710fdc       33.641483   

   Venue Longitude      Venue Category  
0      -117.772800                Café  
1      -117.772800  Italian Restaurant  
2      -117.772006                Food  
3      -117.772800                Café  
4      -117.772800  Italian Restaurant

In [10]:
OC_venues[['Zip', 'Venue']].groupby('Zip').count()

Venue
Zip         
90620      2
90621      9
90622      3
90623      9
90624      3
90630      8
90631      5
90632      3
90633      3
90680      5
90721      3
90740     10
92602      2
92604      3
92605      3
92607      3
92612      1
92614      2
92615      3
92616      3
92618     10
92619     20
92620     20
92623     26
92626     17
92627     10
92628      3
92629      5
92630      2
92635      3
92646      1
92647     13
92648      1
92649      4
92651     15
92652      3
92654      1
92656      8
92658      3
92659      2
92661     26
92662     10
92663     23
92670     11
92672     45
92673      1
92674     19
92675     38
92680     13
92683      4
92684      3
92685      3
92688      4
92690      3
92691      2
92697      3
92698      3
92701     29
92702      3
92703      6
92704      9
92706      1
92707      7
92708      8
92709      3
92710      4
92711      3
92712      3
92728      3
92735      3
92780     67
92781      3
92782      4
92799      3
92801      2
92802     36
92803      3
92804     20
92806      7
92807     19
92808      9
92812      3
92814      3
92815      3
92816      3
92817      3
92821      7
92822      3
92825      3
92831      2
92832     19
92833     14
92834      3
92835      5
92836      3
92837      3
92838      3
92840      2
92841      3
92842      3
92843      4
92844      6
92845     11
92846      3
92850      3
92856      3
92857      3
92859      3
92861      4
92862      3
92863      3
92864      3
92865      3
92866      3
92867      3
92868     15
92869      1
92871      3
92885      3
92886      2
92887      2
92899      3

In [11]:
venue_count = OC_venues[['City', 'Venue Category']].groupby('City').count().rename(columns={'Venue Category' : 'Count'}).sort_values(['Count'], ascending=False)
#OC_venues[(OC_venues['Venue Category'] == 'Food') & (OC_venues['Venue'] != 'Marie Callendar\'s')]
venue_count.reset_index(inplace=True)
venue_count['City'] = venue_count['City'].str.upper()
venue_count

City  Count
0                  ANAHEIM    120
1                   IRVINE     97
2                   TUSTIN     74
3                SANTA ANA     67
4             SAN CLEMENTE     65
5            NEWPORT BEACH     64
6                FULLERTON     52
7             GARDEN GROVE     45
8                   ORANGE     43
9      SAN JUAN CAPISTRANO     38
10              COSTA MESA     30
11        HUNTINGTON BEACH     25
12            LAGUNA BEACH     18
13              BUENA PARK     17
14               PLACENTIA     14
15                LA HABRA     11
16         FOUNTAIN VALLEY     11
17             ALISO VIEJO     11
18              SEAL BEACH     10
19             WESTMINSTER     10
20                    BREA     10
21                LA PALMA      9
22                 CYPRESS      8
23             YORBA LINDA      7
24           MISSION VIEJO      5
25                 STANTON      5
26              DANA POINT      5
27  RANCHO SANTA MARGARITA      4
28            LAGUNA HILLS      4
29              VILLA PARK      4
30            LOS ALAMITOS      3
31           LAGUNA NIGUEL      3
32             LAKE FOREST      2

#### The GeoJSON file for Orange County is downloaded

In [12]:
!wget --quiet https://opendata.arcgis.com/datasets/60119fce76d74dc08c3aa455f34b2b4d_0.geojson -O orange_county.json

print('GeoJSON file downloaded!')

GeoJSON file downloaded!


A choropleth map is created to show the relative frequency of venues for each city and the locations of the zip codes are also displayed.

In [13]:
OC_geo = r'orange_county.json' # geojson file

# create a plain world map
OC_map = folium.Map(location=[latitude, longitude], zoom_start=10)

OC_map.choropleth(
    geo_data=OC_geo,
    data=venue_count,
    columns=['City', 'Count'],
    key_on = 'feature.properties.CITY', 
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Orange County'
)

# add markers to map
for lat, lng, city, zipCode in zip(df['Latitude'], df['Longitude'], df['City'], df['Zip']):
    label = '{}, {}'.format(city, zipCode)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(OC_map)  

# display map
OC_map

A dataframe is used to show the frequency of the different venue categories in Orange County.

In [14]:
venue_types = OC_venues[['Venue Category', 'Venue']].groupby('Venue Category').count().rename(columns={'Venue' : 'Count'}).sort_values(['Count'], ascending=False)
venue_types.reset_index(inplace=True)
venue_types

Venue Category  Count
0                            Food     72
1                            Café     69
2              Italian Restaurant     67
3              Mexican Restaurant     63
4            Fast Food Restaurant     61
5                     Pizza Place     51
6             American Restaurant     48
7                          Bakery     35
8                  Sandwich Place     32
9               Korean Restaurant     26
10            Japanese Restaurant     23
11                     Food Truck     22
12               Sushi Restaurant     22
13                     Restaurant     20
14               Asian Restaurant     20
15             Chinese Restaurant     19
16       Mediterranean Restaurant     17
17                 Breakfast Spot     15
18                   Burger Joint     15
19          Vietnamese Restaurant     13
20                Thai Restaurant     13
21             Seafood Restaurant     11
22                      BBQ Joint     10
23                     Taco Place     10
24                    Snack Place     10
25            Fried Chicken Joint      9
26                     Donut Shop      9
27                  Hot Dog Joint      8
28                   Noodle House      7
29                  Deli / Bodega      7
30                     Poke Place      7
31                          Diner      6
32  Vegetarian / Vegan Restaurant      6
33        New American Restaurant      6
34                     Bagel Shop      5
35              Indian Restaurant      5
36      Cajun / Creole Restaurant      4
37                      Gastropub      4
38                  Burrito Place      4
39                     Food Court      3
40      Middle Eastern Restaurant      3
41               Tapas Restaurant      3
42              French Restaurant      2
43                         Buffet      2
44      Latin American Restaurant      2
45                     Steakhouse      2
46              Fish & Chips Shop      2
47             Tex-Mex Restaurant      2
48               Ramen Restaurant      2
49                     Soup Place      1
50        South Indian Restaurant      1
51      South American Restaurant      1
52              Afghan Restaurant      1
53             Persian Restaurant      1
54              Hotpot Restaurant      1
55            Hawaiian Restaurant      1
56             African Restaurant      1
57                     Food Stand      1
58              Fondue Restaurant      1
59             English Restaurant      1
60            Dumpling Restaurant      1
61             Dim Sum Restaurant      1
62        Comfort Food Restaurant      1
63                      Cafeteria      1
64         Argentinian Restaurant      1
65              German Restaurant      1

## Methodology <a name="methodology"></a>
This project's main focus is to find the best location to start a new restaurant based on information obtained for Foursquare. We will mainly be looking at the ratings and the frequency at which they appear in the different cities.

In our first step, we collected data on location and type of every venue within 2km from each zip code geospatial coordinate and identified all the venues that are restaurants.

The second step is to choose a restaurant type from the list above to analyze. For an example, we will be using Sushi Restaurant. With this, we can create a choropleth map to visualize what locations have higher density of sushi restaurants and where they are located using their geospatial data gathered from the Foursquare API.

Finally, we will be creating a ranking system in order to find the best city to start a new sushi restaurant in. This will be done using the rating data gathered from the Foursquare API. In order to find the best restuarant, we will be looking at two different factors: 
* The number of venues that have an above average rating in the city
* The average rating of all the locations within the city.
With the best city chosen, we can then generate a list of all zip codes within that city.

## Analysis <a name="analysis"></a>
We can now choose which type of venue we want(Sushi Restaurant for our example) to analyze and a dataframe of all the locations and the city they are in will be generated.

In [15]:
# Obtaining venue categories into an array of strings instead of objects
ObjArray = venue_types[['Venue Category']].to_numpy()
venue_array=[]
for i in ObjArray:
    venue_array = np.append(ObjArray, i[0])

    
print("Enter a venue category listed above")    

flag=0
while flag == 0:
    user_input = input()
    if(user_input in venue_array):
        print('The venue you chose is: ' + user_input)
        flag = 1
    else:
        print('Either the venue you chose is not listed or the venue may not have been spelled correctly. Keep in mind this is case sensitive.')
    




selected_venues = OC_venues[(OC_venues['Venue Category'] == user_input)].reset_index(drop=True)
selected_count = selected_venues[['City', 'Venue']].groupby('City').count().rename(columns={'Venue' : 'Count'}).sort_values(['Count'], ascending=False)
selected_count.reset_index(inplace=True)
selected_count['City'] = selected_count['City'].str.upper()
selected_count

Enter a venue category listed above
Sushi Restaurant
The venue you chose is: Sushi Restaurant


City  Count
0         SAN CLEMENTE      7
1               TUSTIN      5
2            FULLERTON      2
3               IRVINE      2
4           COSTA MESA      1
5      FOUNTAIN VALLEY      1
6     HUNTINGTON BEACH      1
7         LAGUNA BEACH      1
8        NEWPORT BEACH      1
9  SAN JUAN CAPISTRANO      1

We can now create a Choropleth map to visualize where the locations are at. The locations of the restaurants are also shown as well.

In [16]:
# create a plain world map
selected_map = folium.Map(location=[latitude, longitude], zoom_start=10)

selected_map.choropleth(
    geo_data=OC_geo,
    data=selected_count,
    columns=['City', 'Count'],
    key_on = 'feature.properties.CITY', 
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Orange County'
)

# add markers to map
for lat, lng, city, zipCode in zip(selected_venues['Venue Latitude'], selected_venues['Venue Longitude'], selected_venues['City'], selected_venues['Zip']):
    label = '{}, {}'.format(city, zipCode)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=1.0,
        parse_html=False).add_to(selected_map)  

# display map
selected_map

Now we will be creating an array of the ratings for each of the venues and appending to the dataframe of the locations. If there is no rating, then NaN will be added.

In [17]:
venues_ids= selected_venues['Venue ID']
ratings=[]
for venue_id in venues_ids.values.tolist():
    url = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}'.format(
                venue_id, 
                CLIENT_ID, 
                CLIENT_SECRET, 
                VERSION)
    
    result = requests.get(url).json()
    try:
        venues_rating=result['response']['venue']['rating']
        ratings=np.append(ratings, venues_rating)
    except KeyError:
        ratings = np.append(ratings, np.nan)
ratings

array([7.3, nan, nan, 6.7, nan, nan, nan, 6.9, 9. , 6.8, 5.9, nan, nan,
       7.8, 7.1, 7.3, nan, nan, 7.7, 7.9, 5.5, 8. ])

In [18]:
selected_venue_df = selected_venues.assign(Rating = ratings)
selected_venue_df

City    Zip  Neighborhood Latitude  Neighborhood Longitude  \
0   San Juan Capistrano  92675              33.500843             -117.658660   
1       Fountain Valley  92708              33.708618             -117.956290   
2      Huntington Beach  92649              33.720017             -118.046140   
3                Irvine  92623              33.686519             -117.830788   
4                Irvine  92623              33.686519             -117.830788   
5          San Clemente  92674              33.438428             -117.623131   
6          San Clemente  92674              33.438428             -117.623131   
7            Costa Mesa  92627              33.647028             -117.915060   
8          San Clemente  92672              33.427078             -117.614010   
9          San Clemente  92672              33.427078             -117.614010   
10         San Clemente  92672              33.427078             -117.614010   
11         San Clemente  92672              33.427078             -117.614010   
12         San Clemente  92672              33.427078             -117.614010   
13               Tustin  92780              33.741651             -117.821270   
14               Tustin  92780              33.741651             -117.821270   
15               Tustin  92780              33.741651             -117.821270   
16               Tustin  92780              33.741651             -117.821270   
17               Tustin  92780              33.741651             -117.821270   
18        Newport Beach  92661              33.601822             -117.899660   
19            Fullerton  92833              33.874314             -117.963700   
20            Fullerton  92833              33.874314             -117.963700   
21         Laguna Beach  92651              33.535325             -117.771920   

                                Venue                  Venue ID  \
0               Oeeshi Japanese Grill  4af62fd6f964a5200a0222e3   
1                           Duo Sushi  4dee9aea7d8be635ea67ed68   
2                        Shogun Sushi  4b842fc4f964a5204a2631e3   
3                      Kura Sushi Bar  4ab19cd4f964a520386a20e3   
4                          Kiku Sushi  57c9dbde498e0875ec2dcd57   
5                          Nobu Sushi  548de7a4498edc77fcf008b6   
6                          Nobu Sushi  4c255b28f7ced13acb85246d   
7                          Sushi Wave  4ba04360f964a520ea6437e3   
8                       9 Style Sushi  4b6b9fe7f964a5201f132ce3   
9                        Sushi Taka-O  4bc13b28f8219c748e28b310   
10                          Aha Sushi  53044a44498e8936e4df43a8   
11                 Sushi Gallery Miki  4bc3deffb492d13aeb6ea960   
12                     Muse Sushi Bar  565bad3c498e2696eaafb1e2   
13  Tommy's Sushi Japanese Restaurant  4b62560bf964a520f9422ae3   
14                        Gohan Sushi  52d399ef498e85dd058d205a   
15                         Sushi Damu  5711b7d6cd10bf624edbb94b   
16                         Sushi Dama  56f8a96bcd106d63a33c7911   
17                           Kitajima  4bde4f376198c9b692b213ff   
18                         San Shi Go  4b3d521ef964a5205a9225e3   
19                               Sato  4b64efedf964a520fdda2ae3   
20               Hoshi Sushi & Lounge  5573c1d8498e842193845243   
21                         San Shi Go  4aa4762bf964a520e04620e3   

    Venue Latitude  Venue Longitude    Venue Category  Rating  
0        33.497791      -117.660919  Sushi Restaurant     7.3  
1        33.710296      -117.954844  Sushi Restaurant     NaN  
2        33.721658      -118.042222  Sushi Restaurant     NaN  
3        33.688542      -117.833569  Sushi Restaurant     6.7  
4        33.688826      -117.834683  Sushi Restaurant     NaN  
5        33.437515      -117.624580  Sushi Restaurant     NaN  
6        33.437275      -117.624895  Sushi Restaurant     NaN  
7        33.650178      -117.911336  Sushi Restaurant     6.9  
8        33.426197      -117.612431  

To make the data easier to analyze, we can clean up the data by removing all the NaN values and grouping by city. This will allow us to see how many restaurants with valid ratings are in each city

In [19]:
clean_venues = selected_venue_df.dropna()

#Check if clean_venues is empty after getting rid of NaN values
if clean_venues.empty:
    print('There are no venues of this type that have ratings. Thus, there is not enough information to properly address the problem. \n It is recommended to choose a different venue category.')

clean_count = clean_venues[['City', 'Rating']].groupby('City').count().rename(columns={'Rating' : 'Count'}).sort_values(['Count'], ascending=False)
clean_count.reset_index(inplace=True)
clean_count['City'] = clean_count['City'].str.upper()

clean_count

City  Count
0         SAN CLEMENTE      3
1               TUSTIN      3
2            FULLERTON      2
3           COSTA MESA      1
4               IRVINE      1
5         LAGUNA BEACH      1
6        NEWPORT BEACH      1
7  SAN JUAN CAPISTRANO      1

Here we can create a choropleth map of the remaining locations to visualize which areas have more of this type of venue.

In [20]:
# create a plain world map
selected_map = folium.Map(location=[latitude, longitude], zoom_start=10)

selected_map.choropleth(
    geo_data=OC_geo,
    data=clean_count,
    columns=['City', 'Count'],
    key_on = 'feature.properties.CITY', 
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Orange County'
)

# add markers to map
for lat, lng, city, zipCode in zip(clean_venues['Venue Latitude'], clean_venues['Venue Longitude'], clean_venues['City'], clean_venues['Zip']):
    label = '{}, {}'.format(city, zipCode)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=1.0,
        parse_html=False).add_to(selected_map)  

# display map
selected_map

We can calculate the average rating over all the locations to have a reference point on how each individual restaurant is performing compared to all.

In [21]:
avg_Selected_Rating= round(selected_venue_df['Rating'].mean(), 2)
avg_Selected_Rating

7.22

### Recommendation System
This is where we create the ranking system to find the best location for a new restaurant based on the performance of known restaurants. The ranking system takes into account two factors: 
* The number of venues that have an above average rating in the city
* The average rating of all the locations within the city.

These values are normalized using min-max normalization and the two numbers are averaged. The higher the number, the better it is to be recommended. The values of the final score will range from 0 to 1 where 0 is not likely to recommend and 1 is highly likely to recommend.


In [22]:
#Averge rating per city
rating_avg = selected_venue_df[['City', 'Rating']].groupby('City').mean().rename(columns={'Rating' : 'Rating Average'})

#Number of rated venues per city
rating_count = selected_venue_df[['City', 'Rating']].groupby('City').count().rename(columns={'Rating' : 'Number of venues with ratings'})

#Merging both dataframes into one and dropping NaN rows
rating_df = pd.merge(rating_avg, rating_count, on=['City']).dropna()

#Number of venues greater than overall average rating
abv_avg_rating = selected_venue_df[['City', 'Rating']][(selected_venue_df['Rating'] > avg_Selected_Rating)].groupby('City').count().rename(columns={'Rating' : 'Number of venues with ratings above average'})

#Merging dataframe with raitng_df
rating_df = pd.merge(rating_df, abv_avg_rating, on=['City'], how='left').fillna(0)

#Calculating Normalization of venues are above average and appending to dataframe
rating_df['Normalized venues above average'] = ((rating_df['Number of venues with ratings above average'] - rating_df['Number of venues with ratings above average'].min()) / (rating_df['Number of venues with ratings above average'].max() - rating_df['Number of venues with ratings above average'].min()))

#Calculating Normalization of Rating Average and appending to dataframe
rating_df['Normalized rating average'] = ((rating_df['Rating Average'] - rating_df['Rating Average'].min()) / (rating_df['Rating Average'].max() - rating_df['Rating Average'].min()))

rating_df

Rating Average  Number of venues with ratings  \
City                                                                 
Costa Mesa                 6.900000                              1   
Fullerton                  6.700000                              2   
Irvine                     6.700000                              1   
Laguna Beach               8.000000                              1   
Newport Beach              7.700000                              1   
San Clemente               7.233333                              3   
San Juan Capistrano        7.300000                              1   
Tustin                     7.400000                              3   

                     Number of venues with ratings above average  \
City                                                               
Costa Mesa                                                   0.0   
Fullerton                                                    1.0   
Irvine                                                       0.0   
Laguna Beach                                                 1.0   
Newport Beach                                                1.0   
San Clemente                                                 1.0   
San Juan Capistrano                                          1.0   
Tustin                                                       2.0   

                     Normalized venues above average  \
City                                                   
Costa Mesa                                       0.0   
Fullerton                                        0.5   
Irvine                                           0.0   
Laguna Beach                                     0.5   
Newport Beach                                    0.5   
San Clemente                                     0.5   
San Juan Capistrano                              0.5   
Tustin                                           1.0   

                     Normalized rating average  
City                                            
Costa Mesa                            0.153846  
Fullerton                             0.000000  
Irvine                                0.000000  
Laguna Beach                          1.000000  
Newport Beach                         0.769231  
San Clemente                          0.410256  
San Juan Capistrano                   0.461538  
Tustin                                0.538462

In [23]:
final_rating_score = ( (rating_df['Normalized venues above average'] + rating_df['Normalized rating average']) / 2).to_frame()
final_rating_score.columns = ['Final Score']
final_rating_score = final_rating_score.sort_values(['Final Score'], ascending=False)
final_rating_score

Final Score
City                            
Tustin                  0.769231
Laguna Beach            0.750000
Newport Beach           0.634615
San Juan Capistrano     0.480769
San Clemente            0.455128
Fullerton               0.250000
Costa Mesa              0.076923
Irvine                  0.000000

## Results and Discussion <a name="results"></a>
From our recommendation system, we found that the best location for a new sushi restaurant is Tustin with a final score of about 0.78. We also can see that Laguna Beach is close behind with 0.75 and Newport Beach is 0.63. With this information we can conclude that the sushi restaurants in Tustin perform the highest, but we can also see that there is a higher frequency of sushi restaurants that are in coastal cities versus inland cities. This can mean that in addition to Tustin as a recommended location, we could also recommend that coastal cities are a good place for sushi restaurants. This makes sense as the fish will be more fresh and higher quality if they are closer to the ocean. Finally, we can create a list of all the zip codes in Tustin along with their latitude and longitudes, which is shown in the following cell.

However, our recommendation system only takes into account a few factors that should be accounted for. Therefore, this should only be taken as a staring point from which to start a new restaurant from where more consideration should be taken before settling on a final location.

In [24]:
try:
    best_location = final_rating_score.index[0]
    print(df[df['City'] == best_location].head())
except IndexError:
    print('There is not enough data to determine the best location.')

       Zip    City   Latitude   Longitude
62   92781  Tustin  33.640302 -117.769442
82   92780  Tustin  33.741651 -117.821270
126  92782  Tustin  33.739571 -117.786180


## Conclusion <a name="conclusion"></a>
The purpose of this project was to recommend a city location in Orange County for a specific type of restaurant as well as zip codes within the city limits. As an example, the restaurant type chosen was sushi restaurants. We first gathered restaurants of all types using the Foursquare API and then filtered out by our choice(Sushi Restaurant). To gather rating information on each location, we again used the Foursquare API and then proceeded to filter out restaurants with NaN values for their rating as they were not useful to our analysis. We then were able to create a ranking system based off the rating data and find the best location. For our example(Sushi Restaurant), the best location we found was Tustin. With this information, the zip codes in Tustin were given as potential new locations to start a new sushi restaurant.

The recommendation system is very basic and can be improved to be more sucessful by adding more relevant factors into account. Some factors that could provide to be useful are demographics of the region, locations of vacant buildings and their pricing, and using different performance metrics for restaurants such as total profit. In the end, this should only be used as a starting point as to which a new restaurant location will be chosen.